Assume that you have run five display ad campaigns, each with 1000 exposures. The data are given here in the same format as in the in-class example: the raw clicks data are in clicks.dataset.2.xlsx and the post-click transaction profit volumes are in volumes.dataset.2.xlsx.

In [1]:
import pandas as pd
import jax
import jax.numpy as jnp
import pandas as pd
import numpy as np
from scipy import stats
import plotly.express as px
import jax
import jax.numpy as jnp
import pandas as pd
import plotly.express as px
import pandas as pd
import plotly.express as px
import jax.scipy.special as jsp
# from jax.experimental import stax

dataVol = pd.read_csv("./Data/volumes.dataset.2.csv")
dataClicks=pd.DataFrame(data={'ad':[1,2,3,4,5],'clicks':[52,38,51,45,25]})
total_clicks = 1_000
n_samples = 100_000
VolumeD= pd.read_csv('./Data/volumes.dataset.2.csv')
VolumeDjnp = jnp.array(VolumeD)

Metal device set to: Apple M3 Pro

systemMemory: 18.00 GB
maxCacheSize: 6.00 GB



W0000 00:00:1745049211.781786  312701 mps_client.cc:510] WARNING: JAX Apple GPU support is experimental and not all JAX functionality is correctly supported!
I0000 00:00:1745049211.791766  312701 service.cc:145] XLA service 0x120e6a3e0 initialized for platform METAL (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1745049211.791774  312701 service.cc:153]   StreamExecutor device (0): Metal, <undefined>
I0000 00:00:1745049211.793011  312701 mps_client.cc:406] Using Simple allocator.
I0000 00:00:1745049211.793021  312701 mps_client.cc:384] XLA backend will use up to 12884443136 bytes on device 0 for SimpleAllocator.


In [2]:
# ---------------------------
# INPUTS
# ---------------------------

successes = jnp.array(dataClicks['clicks'])  # Success clicks for Product A, B, C
# RNG setup
key = jax.random.PRNGKey(100)
keys = jax.random.split(key, num=5)

# Step 1: Initial Prior (assume prior knowledge or weak prior)
alpha_prior = 1  # 1 success
beta_prior = 1   # 1 failure → equivalent to uniform

# Function to compute Beta PDF
def beta_pdf(x, alpha, beta):
    x=jnp.array(x)
    return (x**(alpha - 1)) * ((1 - x)**(beta - 1)) / jsp.beta(alpha, beta)

# ---------------------------
# SIMULATE BETA DISTRIBUTIONS
# ---------------------------
samples = []
ctrMatrix=jnp.empty(100000).reshape(-1,1)
# ctrMatrixProb=jnp.empty(100000).reshape(-1,1)
for i in range(5):
    alpha_post = alpha_prior+successes[i]
    beta_post = beta_prior + (total_clicks - successes[i])
    x= jax.random.beta(keys[i], a=alpha_post, b=beta_post, shape=(n_samples,))
    # samples.append(x)
    # ctrMatrix =jnp.concatenate(x.reshape(-1,1))
    # samples = jnp.array(samples)
    # Compute PDF values for these samples
    # probabilities=jax.scipy.stats.beta.pdf(jnp.array(x),alpha_post,beta_post)/n_samples
    ctrMatrix =jnp.concatenate([ctrMatrix,x.reshape(-1,1)],axis=1)
    # ctrMatrixProb =jnp.concatenate([ctrMatrixProb,probabilities.reshape(-1,1)],axis=1)
    # probabilities = beta_pdf(samples, alpha_post, beta_post)


# Stack into shape (n_samples, 3)
# samples= jnp.array(samples)
# probabilities = jnp.array(probabilities)
# ctrMatrix = jnp.stack([samples,probabilities], axis=1)  # (10000, 3)
ctrMatrix = ctrMatrix[:,1:]
# ctrMatrixProb = ctrMatrixProb[:,1:]
# Pick product with highest CTR per sample
winner_index = jnp.argmax(ctrMatrix[:,1:], axis=1)  # (10000,)

# Count wins for each product
product_wins = jnp.bincount(winner_index, length=5)

# ---------------------------
# CONVERT TO TRANSACTION VOLUME
# ---------------------------
# For each sample, take CTR of winning product and multiply by audience
winning_ctrs = jnp.take_along_axis(ctrMatrix, winner_index[:, None], axis=1).squeeze()
# ---------------------------
# VISUALIZATION
# ---------------------------
# Convert to DataFrame
ctrDF = pd.DataFrame({
    'Winning CTR': winning_ctrs,
    'Winning Product': winner_index,
})

productmapDict={0:'Ad 1',1:'Ad 2',2:'Ad 3',3:'Ad 4',4:'Ad 5'}

ctrDF['AdCampaign']=ctrDF['Winning Product'].apply(lambda x: productmapDict[x])
# Bar chart for win counts
df_count = pd.DataFrame({
    'Product': ['Ad 1', 'Ad 2', 'Ad 3','Ad 4','Ad 5'],
    'Wins': list(map(int, product_wins))
})

fig1 = px.bar(df_count, x='Product', y='Wins', title="Winning Counts (Higher CTR in Each Customer)", text='Wins')
fig1.update_layout(template="plotly_white")
fig1.show()
#fig1 = px.bar(ctrDF, x='Winning CTR', color='Winning Product', title="Winning Counts (Higher CTR in Each Customer)", text='Winning CTR')
#fig1.update_layout(template="plotly_white")
#fig1.show()

# Histogram of Transaction Volumes
fig2 = px.histogram(ctrDF, x='Winning CTR', nbins=70,color='AdCampaign',
                    title="Predicted Winning CTR Distribution (Winning Click Through Rates)",
                    labels={'Transaction Volume': 'Predicted Buys'})
fig2.update_layout(template="plotly_white")
fig2.show()

In [3]:
ctrMatrix.shape

(100000, 5)

In [4]:
# ---- Step 2: Generate T-distribution samples per ad ----
samples_dict = {}
n_samples = 100_000

for ad_id, group in VolumeD.iloc[:,1:].groupby('ad'):
    volumes = group['volume'].values
    mean = np.mean(volumes)
    std = np.std(volumes, ddof=1)
    dfree = len(volumes) - 1

    # Sample from T-distribution
    t_samples = stats.t.rvs(dfree, loc=mean, scale=std, size=n_samples,random_state=100)
    samples_dict[ad_id] = np.clip(t_samples,0,None)

# ---- Step 3: Flatten for visualization ----
flat_samples = []

for ad_id, samples in samples_dict.items():
    flat_samples.extend([{'ad': ad_id, 'VolumeOfAds': np.ceil(v)} for v in samples])

AdVolData = pd.DataFrame(flat_samples)


In [5]:
# Step 1: Create a sample index column (same for each ad)
AdVolData['Ad_index'] = AdVolData.groupby('ad').cumcount()

# Step 2: Pivot table: rows = sample_index, columns = ad, values = volume
pivot_df = AdVolData.pivot(index='Ad_index', columns='ad', values='VolumeOfAds')

# Step 3: For each sample_index, find which ad had the highest volume
pivot_df['PrefAd'] = pivot_df.idxmax(axis=1)  # This gives the ad with highest volume

# Step 4: Count how many times each ad was sold
sold_counts = pivot_df['PrefAd'].value_counts().sort_index()

# Step 5: Display results
sold_counts_df = sold_counts.reset_index()
sold_counts_df.columns = ['Ad', 'PrefCstCount']
# print(sold_counts_df)

In [6]:
fig1 = px.bar(sold_counts_df, x='Ad', y='PrefCstCount', title="Customer Count with Higher Volume in Each Ad", text='PrefCstCount')
fig1.update_layout(template="plotly_white")
fig1.show()

# Histogram of Transaction Volumes
fig2 = px.histogram(AdVolData, x='VolumeOfAds', nbins=200,color='ad',
                    title="Distribution Volume of Ads across 5 ads",
                    labels={'Transaction Volume': 'Predicted Buys'})
fig2.update_layout(template="plotly_white")
fig2.show()

In [7]:
pivot_df.head(10)

ad           1     2     3     4      5  PrefAd
Ad_index                                       
0         25.0  28.0  19.0  25.0   39.0       5
1         46.0  65.0  48.0  54.0  104.0       5
2         45.0  62.0  46.0  52.0   99.0       5
3         36.0  47.0  34.0  40.0   72.0       5
4         38.0  50.0  36.0  42.0   78.0       5
5         37.0  47.0  34.0  40.0   71.0       5
6         38.0  49.0  36.0  42.0   77.0       5
7         51.0  73.0  54.0  60.0  118.0       5
8         57.0  82.0  62.0  67.0  132.0       5
9         38.0  51.0  37.0  43.0   78.0       5

In [8]:
jnp.array(pivot_df.iloc[:,:-1])

Array([[ 25.,  28.,  19.,  25.,  39.],
       [ 46.,  65.,  48.,  54., 104.],
       [ 45.,  62.,  46.,  52.,  99.],
       ...,
       [ 46.,  69.,  31.,  51., 112.],
       [ 49.,  48.,  47.,  30.,  68.],
       [ 34.,  28.,  57.,  45.,  71.]], dtype=float32)

In [9]:
FinalArray=jnp.concatenate([ctrMatrix,jnp.array(pivot_df.iloc[:,:-1]),ctrMatrix*jnp.array(pivot_df.iloc[:,:-1])],axis=1)

In [10]:
FinalArray.shape

(100000, 15)

In [11]:
winner_index = jnp.argmax(FinalArray[:,-5:], axis=1)  # (10000,)
winner_index
FinalArrayPrd=jnp.concatenate([FinalArray,winner_index.reshape(-1,1)],axis=1)
FinalArrayPrd

Array([[0.04453314, 0.04091809, 0.0498407 , ..., 1.1637726 , 1.3455595 ,
        4.        ],
       [0.05589054, 0.0443718 , 0.0472265 , ..., 2.7623901 , 2.5773504 ,
        1.        ],
       [0.04571863, 0.03855507, 0.05297022, ..., 2.7052093 , 2.498679  ,
        3.        ],
       ...,
       [0.05867663, 0.03958387, 0.054184  , ..., 1.8378441 , 2.6023417 ,
        1.        ],
       [0.05739125, 0.04532875, 0.04184928, ..., 1.507901  , 1.0591594 ,
        0.        ],
       [0.047384  , 0.03461643, 0.06053988, ..., 1.9237819 , 1.7444296 ,
        2.        ]], dtype=float32)

In [12]:
product_wins = jnp.bincount(FinalArrayPrd[:,-1].astype(int),length=5)
FinalDF= pd.DataFrame(FinalArrayPrd)

FinalDF['AdCampaign']=FinalDF.iloc[:,-1].apply(lambda x: productmapDict[x])
# Bar chart for win counts
Muldf_count = pd.DataFrame({
    'Product': ['Ad 1', 'Ad 2', 'Ad 3','Ad 4','Ad 5'],
    'Wins': list(map(int, product_wins))
})

fig1 = px.bar(Muldf_count, x='Product', y='Wins', title="Winning Counts (Higher CTR in Each Customer)", text='Wins')
fig1.update_layout(template="plotly_white")
fig1.show()
#fig1 = px.bar(ctrDF, x='Winning CTR', color='Winning Product', title="Winning Counts (Higher CTR in Each Customer)", text='Winning CTR')
#fig1.update_layout(template="plotly_white")
#fig1.show()

# Histogram of Transaction Volumes
# flattendArray =jnp.reshape(FinalArrayPrd[:,-5:],(-1,))
num_rows, num_cols = FinalArrayPrd[:,-6:-1].shape
# Flatten values row-wise
values = FinalArrayPrd[:,-6:-1].reshape(-1)  # shape (12,)
# Repeat column indices for each row
col_indices = jnp.tile(jnp.arange(num_cols), reps=(num_rows,))  # shape (12,)
# Stack into final array
FinalArrayPrdmelted = jnp.stack([col_indices,values ], axis=1)  # shape (12, 2)
FinalArrayPrdmeltedDF= pd.DataFrame(FinalArrayPrdmelted,columns=['ad','Value'])
FinalArrayPrdmeltedDF['AdCampaign']=FinalArrayPrdmeltedDF['ad'].apply(lambda x: productmapDict[x])
fig2 = px.histogram(FinalArrayPrdmeltedDF, x='Value', nbins=70,color='AdCampaign',
                    title="Predicted Winning CTR Distribution (Winning Click Through Rates)",
                    labels={'Transaction Volume': 'Predicted Buys'})
fig2.update_layout(template="plotly_white")

In [13]:
df_count['ProbabilitiesCTR']=df_count.iloc[:,1]/df_count.iloc[:,1].sum(axis=0)
df_count.sort_values('ProbabilitiesCTR',ascending=False)

Product   Wins  ProbabilitiesCTR
1    Ad 2  70246           0.70246
2    Ad 3  25109           0.25109
0    Ad 1   4621           0.04621
3    Ad 4     24           0.00024
4    Ad 5      0           0.00000

In [14]:
sold_counts_df
sold_counts_df['ProbabilitiesVal']=sold_counts_df.iloc[:,1]/sold_counts_df.iloc[:,1].sum(axis=0)
sold_counts_df.sort_values('ProbabilitiesVal',ascending=False)

Ad  PrefCstCount  ProbabilitiesVal
4   5         78572           0.78572
1   2         13907           0.13907
3   4          4548           0.04548
2   3          1627           0.01627
0   1          1346           0.01346

In [15]:
Muldf_count
Muldf_count['ProbabilitiesPrd']=Muldf_count.iloc[:,1]/Muldf_count.iloc[:,1].sum(axis=0)
Muldf_count.sort_values('ProbabilitiesPrd',ascending=False)

Product   Wins  ProbabilitiesPrd
4    Ad 5  28047           0.28047
1    Ad 2  20449           0.20449
2    Ad 3  17593           0.17593
0    Ad 1  17329           0.17329
3    Ad 4  16582           0.16582

In [16]:
FinalProb=pd.concat([df_count,sold_counts_df,Muldf_count],axis=1).T
FinalProb.columns=['Ad 1', 'Ad 2','Ad 3', 'Ad 4','Ad 5']
FinalProb.iloc[[2,5,8],:].T
plot_data = FinalProb.iloc[[2, 5, 8], :].T
plot_data.columns = ['CTR Prob', 'Volume Prob', 'Combined Score']

# Plot
fig = px.line(
    plot_data,
    markers=True,
    title='Probabilities of Campaign with CTR and Volume',
    labels={
        'index': 'Ad Campaigns',
        'value': 'Probability',
        'variable': 'Probabilities'
    }
)

# Make sure x-axis is properly labeled as Ad Campaigns
fig.update_layout(
    xaxis_title='Ad Campaigns',
    yaxis_title='Probabilities',
    template='plotly_white'
)

fig.show()